# NEUFEP-ME study: Functional Data Quality summary images

This document contains the code and interactive images for data quality checks on the 28 participants in this study. The images are interactive.

A reminder of the study setup. Data per participant was collected in a single session. This included  a single T1w image and 6 functional runs in the following order:
1. Rest Run 1
2. Motor Run 1 (right-hand finger tapping)
3. Emotion Run 1 (matching shapes and faces)
4. Rest Run 2
5. Motor Run 2 (imagined right-hand finger tapping)
6. Emotion Run 2 (recalling an emotional event)

Below are images to summarise, for all participants, the:
- [Mean framewise displacement per run](#fig1)
- [Total framewise displacement per run](#fig2)
- [Mean temporal signal-to-noise ratio (in gray matter) per run](#fig3)

The code can be ignored, unless you are really interested in seeing how the images were generated :)

### Import required Python packages

In [50]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import shutil
import glob
import os
from IPython.display import display, set_matplotlib_formats
import plotly
import plotly.graph_objs as go
plotly.offline.init_notebook_mode()
# import ipywidgets as widgets
import plotly.offline as py
from bids import BIDSLayout
import nibabel as nib
from nilearn import plotting
from nilearn.image import load_img

### Load all subjects

In [51]:
bids_dir = '/Volumes/Stephan_WD/NEUFEPME_data_BIDS/'
asset_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/assets/'

all_dirs = next(os.walk(bids_dir))[1]
all_subs = all_dirs.copy()
for dirname in all_subs:
    if 'sub-' not in dirname:
        all_subs.remove(dirname)
print(all_subs)

['sub-001', 'sub-002', 'sub-003', 'sub-004', 'sub-005', 'sub-006', 'sub-007', 'sub-010', 'sub-011', 'sub-012', 'sub-013', 'sub-015', 'sub-016', 'sub-017', 'sub-018', 'sub-019', 'sub-020', 'sub-021', 'sub-022', 'sub-023', 'sub-024', 'sub-025', 'sub-026', 'sub-027', 'sub-029', 'sub-030', 'sub-031', 'sub-032']


In [52]:
all_participants = pd.read_csv(os.path.join(bids_dir, 'participants.tsv'))
parts = list(all_participants['participant_id'])
parts

['sub-001',
 'sub-002',
 'sub-003',
 'sub-004',
 'sub-005',
 'sub-006',
 'sub-007',
 'sub-010',
 'sub-011',
 'sub-012',
 'sub-013',
 'sub-015',
 'sub-016',
 'sub-017',
 'sub-018',
 'sub-019',
 'sub-020',
 'sub-021',
 'sub-022',
 'sub-023',
 'sub-024',
 'sub-025',
 'sub-026',
 'sub-027',
 'sub-029',
 'sub-030',
 'sub-031',
 'sub-032']

In [5]:
parties = [ {'label': sub, 'value': sub} for sub in parts]
parties

[{'label': 'sub-001', 'value': 'sub-001'},
 {'label': 'sub-002', 'value': 'sub-002'},
 {'label': 'sub-003', 'value': 'sub-003'},
 {'label': 'sub-004', 'value': 'sub-004'},
 {'label': 'sub-005', 'value': 'sub-005'},
 {'label': 'sub-006', 'value': 'sub-006'},
 {'label': 'sub-007', 'value': 'sub-007'},
 {'label': 'sub-010', 'value': 'sub-010'},
 {'label': 'sub-011', 'value': 'sub-011'},
 {'label': 'sub-012', 'value': 'sub-012'},
 {'label': 'sub-013', 'value': 'sub-013'},
 {'label': 'sub-015', 'value': 'sub-015'},
 {'label': 'sub-016', 'value': 'sub-016'},
 {'label': 'sub-017', 'value': 'sub-017'},
 {'label': 'sub-018', 'value': 'sub-018'},
 {'label': 'sub-019', 'value': 'sub-019'},
 {'label': 'sub-020', 'value': 'sub-020'},
 {'label': 'sub-021', 'value': 'sub-021'},
 {'label': 'sub-022', 'value': 'sub-022'},
 {'label': 'sub-023', 'value': 'sub-023'},
 {'label': 'sub-024', 'value': 'sub-024'},
 {'label': 'sub-025', 'value': 'sub-025'},
 {'label': 'sub-026', 'value': 'sub-026'},
 {'label': 

### Load required data from BIDS derivatives folder

In [6]:
deriv_dir = os.path.join(bids_dir, 'derivatives')
preproc_dir = os.path.join(deriv_dir, 'fmrwhy-preproc')
qc_dir = os.path.join(deriv_dir, 'fmrwhy-qc')
tasks = ['rest', 'motor', 'emotion']
runs = ['1', '2']
cols_tasksruns = ['rest 1', 'motor 1', 'emotion 1', 'rest 2', 'motor 2', 'emotion 2']
cols_stats = ['tSNR_mean_GM', 'tSNR_mean_WM', 'tSNR_mean_CSF', 'tSNR_mean_brain', 'zscore_mean', 'gcor']
df_fdmean = pd.DataFrame(columns=cols_tasksruns)
df_fdsum = pd.DataFrame(columns=cols_tasksruns)
df_tsnrgm = pd.DataFrame(columns=cols_tasksruns)
df_tsnrwm = pd.DataFrame(columns=cols_tasksruns)
df_tsnrcsf = pd.DataFrame(columns=cols_tasksruns)
df_tsnrbrain = pd.DataFrame(columns=cols_tasksruns)

for sub in all_subs:
    df_fdmean = df_fdmean.append(pd.Series(), ignore_index=True)
    df_fdsum = df_fdsum.append(pd.Series(), ignore_index=True)
    df_tsnrgm = df_tsnrgm.append(pd.Series(), ignore_index=True)
    df_tsnrwm = df_tsnrwm.append(pd.Series(), ignore_index=True)
    df_tsnrcsf = df_tsnrcsf.append(pd.Series(), ignore_index=True)
    df_tsnrbrain = df_tsnrbrain.append(pd.Series(), ignore_index=True)
    
    for task in tasks:
        for run in runs:
            stats_summary_fn = os.path.join(qc_dir, sub, 'func', sub + '_task-' + task + '_run-' + run + '_desc-stats_summary.tsv')
            stats_summary = pd.read_csv(stats_summary_fn, sep='\t')
            fd_fn = os.path.join(preproc_dir, sub, 'func', sub + '_task-' + task + '_run-' + run + '_desc-confounds_fd.tsv')
            fd = pd.read_csv(fd_fn, sep='\t')
            df_fdmean.loc[df_fdmean.index[-1], task + ' ' + run] = np.mean(fd['framewise_displacement'])
            df_fdsum.loc[df_fdsum.index[-1], task + ' ' + run] = np.sum(fd['framewise_displacement'])
            df_tsnrgm.loc[df_tsnrgm.index[-1], task + ' ' + run] = stats_summary.loc[0, 'tSNR_mean_GM']
            df_tsnrwm.loc[df_tsnrwm.index[-1], task + ' ' + run] = stats_summary.loc[0, 'tSNR_mean_WM']
            df_tsnrcsf.loc[df_tsnrcsf.index[-1], task + ' ' + run] = stats_summary.loc[0, 'tSNR_mean_CSF']
            df_tsnrbrain.loc[df_tsnrbrain.index[-1], task + ' ' + run] = stats_summary.loc[0, 'tSNR_mean_brain']

            

In [118]:
# # extract and save data for dash

# fn1 = os.path.join(asset_dir, 'sub-all_task-all_run-all_desc-fdmean.tsv')
# fn2 = os.path.join(asset_dir, 'sub-all_task-all_run-all_desc-fdsum.tsv')
# fn3 = os.path.join(asset_dir, 'sub-all_task-all_run-all_desc-tsnrgm.tsv')
# fn4 = os.path.join(asset_dir, 'sub-all_task-all_run-all_desc-tsnrwm.tsv')
# fn5 = os.path.join(asset_dir, 'sub-all_task-all_run-all_desc-tsnrcsf.tsv')
# fn6 = os.path.join(asset_dir, 'sub-all_task-all_run-all_desc-tsnrbrain.tsv')
# dfs = [df_fdmean, df_fdsum, df_tsnrgm, df_tsnrwm, df_tsnrcsf, df_tsnrbrain]
# tsvs = [fn1, fn2, fn3, fn4, fn5, fn6]

# for dfi, tsvi in zip(dfs, tsvs):
#     dfi.to_csv(tsvi, sep='\t', index=False)

### Load figure data

In [7]:
data1 = []
data2 = []
data3 = []
for i, sub in enumerate(all_subs):
    
    X = np.arange(6)
    Y1 = df_fdmean.iloc[i].to_numpy()
    d1 = go.Scatter(x=X, y=Y1, mode='lines+markers', name=sub, hovertemplate='<b>' + sub + '</b>: %{x}<br>FD mean = %{y:.2f} mm<extra></extra>')
    data1.append(d1)
    
    Y2 = df_fdsum.iloc[i].to_numpy()
    d2 = go.Scatter(x=X, y=Y2, mode='lines+markers', name=sub, hovertemplate='<b>' + sub + '</b>: %{x}<br>FD sum = %{y:.2f} mm<extra></extra>')
    data2.append(d2)
    
    Y3 = df_tsnrgm.iloc[i].to_numpy()
    d3 = go.Scatter(x=X, y=Y3, mode='lines+markers', name=sub, hovertemplate='<b>' + sub + '</b>: %{x}<br>tSNR = %{y:.2f} a.u.<extra></extra>')
    data3.append(d3)

### Display Figure 1
<div id='fig1'></div>

In [8]:
# Fig 1
layout = go.Layout(title='Mean Framewise Displacement',
        xaxis = dict(
            title = 'Runs',
            tickmode = 'array',
            tickvals = [0, 1, 2, 3, 4, 5],
            ticktext = cols_tasksruns
        ),
        yaxis=dict(title='FD in mm'),
        hovermode="closest")
fig1 = go.Figure(data=data1, layout=layout)
py.iplot(fig1)

### Display Figure 2
<div id='fig2'></div>

In [9]:
# Fig 2
layout = go.Layout(title='Total Framewise Displacement',
        xaxis = dict(
            title = 'Runs',
            tickmode = 'array',
            tickvals = [0, 1, 2, 3, 4, 5],
            ticktext = cols_tasksruns
        ),
        yaxis=dict(title='Total FD in mm'))
fig2 = go.Figure(data=data2, layout=layout)
py.iplot(fig2)

### Display Figure 3

<div id='fig3'></div>

In [10]:
# Fig 3
layout = go.Layout(title='Mean tSNR (GM)',
        xaxis = dict(
            title = 'Runs',
            tickmode = 'array',
            tickvals = [1, 2, 3, 4, 5, 6],
            ticktext = cols_tasksruns
        ),
        yaxis=dict(title='Mean tSNR (a.u.)'))
fig3 = go.Figure(data=data3, layout=layout)
py.iplot(fig3)

# Ridge plots for tSNR values in different tissue masks

In [11]:
# Grab tsv files with voxel-wise tsnr data per mask
braintsnr_tsv = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids/derivatives/fmrwhy-multiecho/sub-001/sub-001_task-rest_run-1_echo-2_desc-rapreproc_braintsnr.tsv'
GMtsnr_tsv = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids/derivatives/fmrwhy-multiecho/sub-001/sub-001_task-rest_run-1_echo-2_desc-rapreproc_GMtsnr.tsv'
WMtsnr_tsv = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids/derivatives/fmrwhy-multiecho/sub-001/sub-001_task-rest_run-1_echo-2_desc-rapreproc_WMtsnr.tsv'
CSFtsnr_tsv = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids/derivatives/fmrwhy-multiecho/sub-001/sub-001_task-rest_run-1_echo-2_desc-rapreproc_CSFtsnr.tsv'
df_braintsnr = pd.read_csv(braintsnr_tsv, sep='\t').dropna()
df_GMtsnr = pd.read_csv(GMtsnr_tsv, sep='\t').dropna()
df_WMtsnr = pd.read_csv(WMtsnr_tsv, sep='\t').dropna()
df_CSFtsnr = pd.read_csv(CSFtsnr_tsv, sep='\t').dropna()

In [44]:
# Create ridge plot
import plotly.graph_objects as go
from plotly.colors import sequential, n_colors

dat1 = df_braintsnr['tsnr'].to_numpy()
dat2 = df_GMtsnr['tsnr'].to_numpy()
dat3 = df_WMtsnr['tsnr'].to_numpy()
dat4 = df_CSFtsnr['tsnr'].to_numpy()

layout = go.Layout(title='tSNR distributions for different tissue masks - {sub-001_task-rest_run-1}',
        yaxis = dict(title = 'tSNR distributions in masks'),
        xaxis=dict(title='Temporal signal-to-noise ratio (tSNR)'))

fig = go.Figure(layout=layout)
fig.add_trace(go.Violin(x=dat1, line_color=sequential.Inferno[5], name='Brain'))
fig.add_trace(go.Violin(x=dat2, line_color=sequential.Inferno[6], name='GM'))
fig.add_trace(go.Violin(x=dat3, line_color=sequential.Inferno[7], name='WM'))
fig.add_trace(go.Violin(x=dat4, line_color=sequential.Inferno[8], name='CSF'))
fig.update_traces(orientation='h', side='positive', width=3, points=False)
fig.update_layout(xaxis_showgrid=False, xaxis_zeroline=False)
py.iplot(fig)
fig.write_html("/Users/jheunis/Documents/Websites/rt-me-fmri-dash/assets/tsnr_distributions.html")

In [56]:
# DASH CONTENT html files

deriv_dir = os.path.join(bids_dir, 'derivatives')
preproc_dir = os.path.join(deriv_dir, 'fmrwhy-preproc')
qc_dir = os.path.join(deriv_dir, 'fmrwhy-qc')
me_dir = os.path.join(deriv_dir, 'fmrwhy-multiecho')
asset_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/assets/'
dash_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/'
dash_bids_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids'
dash_deriv_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids/derivatives'
dash_qc_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids/derivatives/fmrwhy-qc'
dash_me_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids/derivatives/fmrwhy-multiecho'

tasks = ['rest', 'motor', 'emotion']
runs = ['1', '2']
cols_tasksruns = ['rest 1', 'motor 1', 'emotion 1', 'rest 2', 'motor 2', 'emotion 2']
cols_stats = ['tSNR_mean_GM', 'tSNR_mean_WM', 'tSNR_mean_CSF', 'tSNR_mean_brain', 'zscore_mean', 'gcor']
# df_fdmean = pd.DataFrame(columns=cols_tasksruns)
# df_fdsum = pd.DataFrame(columns=cols_tasksruns)
# df_tsnrgm = pd.DataFrame(columns=cols_tasksruns)
this_sub = ['sub-001']

for sub in all_subs:
    for task in tasks:
        for run in runs:
            print(sub)
            tsnr_fn = os.path.join(me_dir, sub, 'func', sub + '_task-' + task + '_run-' + run + '_echo-2_space-MNI152_desc-rapreproc_tsnr.nii')
            html_fn = os.path.join(dash_me_dir, sub, sub + '_task-' + task + '_run-' + run + '_echo-2_space-MNI152_desc-rapreproc_tsnr.html')
            img_title = 'tSNR'
            tsnr_img = load_img(tsnr_fn)
            html_view = plotting.view_img(tsnr_img, bg_img=False, cut_coords=[2, -16, 20], title=img_title, black_bg=True, vmax=255)
            html_view.save_as_html(html_fn)

/Users/jheunis/miniconda3/envs/rtme-fmri/lib/python3.7/site-packages/nilearn/image/resampling.py:543: RuntimeWarning:

NaNs or infinite values are present in the data passed to resample. This is a bad thing as they make resampling ill-defined and much slower.

/Users/jheunis/miniconda3/envs/rtme-fmri/lib/python3.7/site-packages/nilearn/image/resampling.py:543: RuntimeWarning:

NaNs or infinite values are present in the data passed to resample. This is a bad thing as they make resampling ill-defined and much slower.

/Users/jheunis/miniconda3/envs/rtme-fmri/lib/python3.7/site-packages/nilearn/image/resampling.py:543: RuntimeWarning:

NaNs or infinite values are present in the data passed to resample. This is a bad thing as they make resampling ill-defined and much slower.

/Users/jheunis/miniconda3/envs/rtme-fmri/lib/python3.7/site-packages/nilearn/image/resampling.py:543: RuntimeWarning:

NaNs or infinite values are present in the data passed to resample. This is a bad thing as they ma

In [23]:
# # Extract and save data for Dash - FD
# dash_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/'
# dash_bids_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids'
# dash_deriv_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids/derivatives'
# dash_qc_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids/derivatives/fmrwhy-qc'

# for sub in all_subs:
#     df_fd = pd.DataFrame(columns=cols_tasksruns)
#     for task in tasks:
#         for run in runs:
#             fd_fn = os.path.join(preproc_dir, sub, 'func', sub + '_task-' + task + '_run-' + run + '_desc-confounds_fd.tsv')
#             fd = pd.read_csv(fd_fn, sep='\t')
#             df_fd[task + ' ' + run] = fd['framewise_displacement']
    
#     os.mkdir(os.path.join(dash_qc_dir, sub))
#     save_fn = os.path.join(dash_qc_dir, sub, sub+'_task-all_run-all_desc-fd.tsv')
#     df_fd.to_csv(save_fn, sep='\t', index=False)


In [43]:
# Extract and save data for Dash - FD into one file
dash_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/'
dash_bids_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids'
dash_deriv_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids/derivatives'
dash_qc_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-dash/bids/derivatives/fmrwhy-qc'

cols_tasksruns = ['rest 1', 'motor 1', 'emotion 1', 'rest 2', 'motor 2', 'emotion 2']
df_fdallsubs = pd.DataFrame(columns=all_subs)

for sub in all_subs:
    allfdlist = []
    fd_fn = os.path.join(dash_qc_dir, sub, sub+'_task-all_run-all_desc-fd.tsv')
    fd = pd.read_csv(fd_fn, sep='\t')
    
    for colname in cols_tasksruns:
        for i in list(fd[colname]):
            allfdlist.append(i)
        allfdlist1 = allfdlist.copy()
        
#         for i in range(208):
#             df_fdallsubs = df_fdallsubs.append({sub: fd.loc[i, colname]}, ignore_index=True)
    
    df_fdallsubs[sub] = allfdlist

df_fdallsubs

saveas_fn = os.path.join(dash_qc_dir, 'sub-all_task-all_run-all_desc-fdallsubs.tsv')
df_fdallsubs.to_csv(saveas_fn, sep='\t', index=False)

# for sub in all_subs:
#     df_fd = pd.DataFrame(columns=cols_tasksruns)
#     for task in tasks:
#         for run in runs:
#             fd_fn = os.path.join(preproc_dir, sub, 'func', sub + '_task-' + task + '_run-' + run + '_desc-confounds_fd.tsv')
#             fd = pd.read_csv(fd_fn, sep='\t')
#             df_fd[task + ' ' + run] = fd['framewise_displacement']
    
#     os.mkdir(os.path.join(dash_qc_dir, sub))
#     save_fn = os.path.join(dash_qc_dir, sub, sub+'_task-all_run-all_desc-fd.tsv')
#     df_fd.to_csv(save_fn, sep='\t', index=False)

In [41]:
# Create violin + data points for FD

sub = 'sub-021'
df_fd = pd.DataFrame(columns=cols_tasksruns)

for task in tasks:
    for run in runs:
        fd_fn = os.path.join(preproc_dir, sub, 'func', sub + '_task-' + task + '_run-' + run + '_desc-confounds_fd.tsv')
        fd = pd.read_csv(fd_fn, sep='\t')
        df_fd[task + ' ' + run] = fd['framewise_displacement']

# df_fd
data = []

layout = go.Layout(title='FD distributions for different functional runs - {sub-001}',
        xaxis = dict(title = 'FD distribution per task and run'),
        yaxis=dict(title='Framewise displacement'))

fig = go.Figure(layout=layout)

i = 0
for colname in cols_tasksruns:
    data.append(df_fd[colname].to_numpy())
    fig.add_trace(go.Violin(y=data[i], line_color=sequential.Inferno[i+3], name=colname, orientation='v', side='positive', width=1.5, points=False, box_visible=True, meanline_visible=True))
    i += 1

fig.update_layout(xaxis_showgrid=False, xaxis_zeroline=False)
py.iplot(fig)

In [20]:
# Create violin + data points for FD for all subs for last run

df_fdsubs = pd.DataFrame(columns=all_subs)
# df_fdsum = df_fdsum.append(pd.Series(), ignore_index=True)
# df_tsnrgm = df_tsnrgm.append(pd.Series(), ignore_index=True)
task = 'emotion'
run = '2'
for sub in all_subs:

    fd_fn = os.path.join(preproc_dir, sub, 'func', sub + '_task-' + task + '_run-' + run + '_desc-confounds_fd.tsv')
    fd = pd.read_csv(fd_fn, sep='\t')
    df_fdsubs[sub] = fd['framewise_displacement']

# df_fd
colors = n_colors('rgb(5, 200, 200)', 'rgb(200, 10, 10)', 28, colortype='rgb')

data = []

layout = go.Layout(title='FD distributions for all subs {task-emotion_run-2}',
        xaxis = dict(title = 'FD distribution', tickangle=45),
        yaxis=dict(title='Framewise displacement'))

fig = go.Figure(layout=layout)

i = 0
for colname, color in zip(all_subs, colors):
    data.append(df_fdsubs[colname].to_numpy())
    fig.add_trace(go.Violin(y=data[i], line_color=color, name=colname, orientation='v', side='positive', width=1.5, points=False, box_visible=True, meanline_visible=True))
    i += 1

fig.update_layout(xaxis_showgrid=False, xaxis_zeroline=False)
py.iplot(fig)

In [42]:
colors = n_colors('rgb(5, 200, 200)', 'rgb(200, 10, 10)', 28, colortype='rgb')

data = []

layout = go.Layout(title='Framewise displacement for all participants over all runs',
        xaxis = dict(title = 'FD distribution', tickangle=45),
        yaxis=dict(title='Framewise displacement (mm)', range=[-0.3, 3]))

fig = go.Figure(layout=layout)

i = 0
for colname, color in zip(all_subs, colors):
    data.append(df_fdallsubs[colname].to_numpy())
    fig.add_trace(go.Violin(y=data[i], line_color=color, name=colname, orientation='v', side='positive', width=1.8, points=False, box_visible=True, meanline_visible=True))
    i += 1

fig.update_layout(xaxis_showgrid=False, xaxis_zeroline=False)
py.iplot(fig)

In [105]:
data

[]

In [21]:
df_fdsubs

sub-001   sub-002   sub-003   sub-004   sub-005   sub-006   sub-007  \
0    0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
1    0.158604  0.179123  0.097846  0.209634  0.118173  0.058234  0.210175   
2    0.170207  0.111452  0.135276  0.135143  0.174530  0.045553  0.209900   
3    0.087987  0.082469  0.071737  0.157527  0.168383  0.096755  0.080294   
4    0.103265  0.081381  0.102272  0.141166  0.189439  0.130944  0.283312   
..        ...       ...       ...       ...       ...       ...       ...   
205  0.188890  0.054099  0.088012  0.269598  0.097310  0.110067  0.165656   
206  0.178439  0.058767  0.095359  0.288137  0.084056  0.123456  0.170590   
207  0.163060  0.088598  0.117996  0.247764  0.085934  0.046326  0.098009   
208  0.094412  0.104779  0.167221  0.216825  0.062273  0.160178  0.123754   
209  0.270279  0.105983  0.133313  0.273568  0.125822  0.109495  0.098153   

      sub-010   sub-011   sub-012  ...   sub-022   sub-023   sub-024  \
0    0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
1    0.604548  0.268459  0.146665  ...  0.097705  0.095736  0.183035   
2    0.538555  0.140356  0.148540  ...  0.166349  0.170073  0.242121   
3    0.440157  0.123029  0.118907  ...  0.078969  0.103500  0.108204   
4    0.338568  0.059271  0.193821  ...  0.040681  0.150012  0.140856   
..        ...       ...       ...  ...       ...       ...       ...   
205  0.142513  0.158469  0.083661  ...  0.361402  0.058452  0.144928   
206  0.239730  0.097971  0.079525  ...  0.193366  0.082158  0.178544   
207  0.258017  0.090941  0.124848  ...  0.298209  0.091921  0.149236   
208  0.245944  0.236093  0.156249  ...  0.117587  0.183173  0.058828   
209  0.578623  0.209606  0.270199  ...  0.069774  0.100854  0.089557   

      sub-025   sub-026   sub-027   sub-029   sub-030   sub-031   sub-032  
0    0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  
1    0.162895  0.140215  0.191617  0.074851  0.231294  0.120889  0.115312  
2    0.140340  0.093503  0.090267  0.075651  0.172085  0.066288  0.140921  
3    0.092619  0.227262  0.122634  0.066402  0.139890  0.165090  0.153069  
4    0.083824  0.180817  0.076278  0.115364  0.121836  0.073769  0.169639  
..        ...       ...       ...       ...       ...       ...       ...  
205  0.153726  0.110991  0.076417  0.097360  0.209329  0.128392  0.039969  
206  0.191660  0.149268  0.023066  0.062299  0.158994  0.067516  0.050799  
207  0.114812  0.103499  0.082761  0.154961  0.097477  0.150753  0.048914  
208  0.135291  0.257626  0.081478  0.096727  0.130595  0.094143  0.112596  
209  0.110955  0.148145  0.104843  0.069013  0.062603  0.114836  0.051243  

[210 rows x 28 columns]

In [22]:
df_fd

rest 1   motor 1  emotion 1    rest 2   motor 2  emotion 2
0    0.000000  0.000000   0.000000  0.000000  0.000000   0.000000
1    0.153360  0.143848   0.158678  0.157551  0.281753   5.860377
2    0.145589  0.132035   0.083306  0.224255  0.175862   1.292329
3    0.121694  0.118647   0.346289  0.108576  0.048935   4.258387
4    0.043415  0.263150   0.270203  0.204272  0.080334   1.356728
..        ...       ...        ...       ...       ...        ...
205  0.430445  0.123099   0.247961  0.670436  0.191736   0.180916
206  0.487243  0.594246   0.127048  0.199568  0.380936   0.128100
207  1.835782  2.324756   0.422666  0.342716  0.112530   0.127022
208  1.276276  2.150514   0.069709  0.589221  0.295696   0.098240
209  0.269579  0.330710   0.089281  0.105586  0.185392   0.124708

[210 rows x 6 columns]